In [1]:
import sys
import os
import glob
import numpy as np
import pandas as pd
import gzip
import matplotlib.pyplot as plt
import plotly
from scipy import stats
from scipy.optimize import curve_fit
import itertools
from collections import Counter
from Bio.Seq import Seq
import functions
import one_rep
import itertools
import function_bio_rep
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from sklearn.cluster import KMeans
from sklearn import preprocessing

In [2]:
global_dir = '/Users/jennysheng/Documents/Chavez_Lab/Yeast_stuff/'
fig_folder = '/Users/jennysheng/Documents/Chavez_Lab/Yeast_stuff/figures/'

sample_dir = '/Users/jennysheng/Documents/Chavez_Lab/Yeast_stuff/sample_spreadsheet_final.csv'
samples = pd.read_csv(sample_dir)

amino_acid_list = ['*', 'A', 'C', 'D', 'E', 'F', 'G', 'H',
                   'I', 'K', 'L', 'M', 'N', 'P', 'Q', 'R',
                   'S', 'T', 'V', 'W', 'Y']
amino_acid_list.reverse()

wt_ = ('SGFRKMAFPSGKVEGCMVQVTCGTTTLNGLWLDDVVYCPRHVICTSEDM'
       'LNPNYEDLLIRKSNHNFLVQAGNVQLRVIGHSMQNCVLKLKVDTANPKTP'
       'KYKFVRIQPGQTFSVLFLNGSCGSVG'
       'FNIDYDCVSFCYMHHMELPTGVHAGTDLEGNFYGPFVDRQTAQAAGTDTT'
       'ITVNVLAWLYAAVINGDRWFLNRFTTTLNDFNLVAMKYNYEPLTQDHVDI'
       'LGPLSAQTGIAVLDMCASLKELLQNGMNGRTILGSALLEDEFTPFDVVRQCSGVTFQ*')
wt_full = ('MSGFRKMAFPSGKVEGCMVQVTCGTTTLNGLWLDDVVYCPRHVICT'
           'SEDMLNPNYEDLLIRKSNHNFLVQAGNVQLRVIGHSMQNCVLKLKV'
           'DTANPKTPKYKFVRIQPGQTFSVLACYNGSPSGVYQCAMRPNFTIK'
           'GSFLNGSCGSVGFNIDYDCVSFCYMHHMELPTGVHAGTDLEGNFYG'
           'PFVDRQTAQAAGTDTTITVNVLAWLYAAVINGDRWFLNRFTTTLND'
           'FNLVAMKYNYEPLTQDHVDILGPLSAQTGIAVLDMCASLKELLQNG'
           'MNGRTILGSALLEDEFTPFDVVRQCSGVTFQ')
wt_ = [x for x in wt_]
wt_full = [x for x in wt_full]

sets = [1, 2, 3, 4, 5, 6, 7, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 8, 9, 10, 'R1']
res_redo = ['8R', '13R1', '13R2', '14R', '16R']

## Replicates

In [18]:
def replicate(rep, replicate_folder, cond_suffix):
    mean_stop = {}
    len_set = {}
    rep1_set = []
    set_list_res = []
    # replicate 1
    for file in sets + res_redo:
        replicate_dir = list(samples[samples['Set']==str(file)][replicate_folder])[0]
        if file in sets:
            fchange = pd.read_csv(replicate_dir + str(file) + '_replicate'+str(rep)+cond_suffix, index_col = [0])
            start = list(samples[samples['Set'] == str(file)]['Start range'])[0]
            end = list(samples[samples['Set'] == str(file)]['End range'])[0]
            fchange.columns = ['Res '+str(x) for x in list(range(start, end))] # name the columns
            wt_subseq = wt_full[start:end] #find WT residues for the set

            flat_list = np.array([item for sublist in fchange.values for item in sublist])
            mean = flat_list[~np.isnan(flat_list)].mean() # mean of the set
            var = flat_list[~np.isnan(flat_list)].var() # variance of the set
            # set the variance of all set to 1
            var_norm = (flat_list-mean)/np.sqrt(var)+mean # normalize the set to unit variance

            fchange_norm = (fchange-mean)/np.sqrt(var) + mean # reshape the flat list to original array
            mean_stop[str(file)] = np.mean(fchange_norm.loc['*']) # add to dict for mean stop
            len_set[str(file)] = len(fchange_norm.columns)
            #new label for columns
            fchange_norm.columns = ['Res '+str(x) for x in list(range(start, end))] # name the columns

            #figure out average wt values for set and linear transform
            cols = fchange_norm.columns
            wt_vals = []
            for row, col in zip(wt_subseq, cols):
                wt_vals.append(fchange_norm.loc[row, col])
            fchange_norm = fchange_norm - np.mean(wt_vals)
            rep1_set.append(fchange_norm)

        elif file in res_redo:
            set_ind = file.find('R') #identify the R notation for the repeated set
            set_redo = file[:set_ind]
            start = list(samples[samples['Set'] == str(file)]['Start range'])[0]
            end = list(samples[samples['Set'] == str(file)]['End range'])[0]
            sites_ = list(samples[samples['Set'] == str(file)]['Sites'])[0]
            sites = ['Res '+ str(x) for x in sites_.split(',')]
            fchange = pd.read_csv(replicate_dir + str(file) + '_replicate'+str(rep)+cond_suffix, index_col = [0])
            fchange.columns = ['Res '+str(x) for x in list(range(start, end))]
            fchange = fchange[sites]
            wt_subseq = [wt_full[int(ind)] for ind in sites_.split(',')] #find WT residues for the set

            flat_list = np.array([item for sublist in fchange.values for item in sublist])
            cols = fchange.columns
            wt_vals = []
            for row, col in zip(wt_subseq, cols):
                wt_vals.append(fchange.loc[row, col])

            # Calculate scaling values for slotting in individual residues
            wt_mean = np.mean(wt_vals)
            stop_mean = np.mean(fchange.loc['*'])
            scale_factor = mean_stop[set_redo]/(stop_mean-wt_mean)
            print(scale_factor)
            fchange_norm = (fchange - wt_mean)*scale_factor

            set_list_res.append(fchange_norm)
        
    return(rep1_set, set_list_res)

## glu/gal condition

#### Replicate 1

In [19]:
rep1_set, set_list_res = replicate(0, 'replicate_folder', '_gal_glu.csv')
all_residues = pd.concat(rep1_set, axis = 1)

all_res_redo = pd.concat(set_list_res, axis = 1)
all_res_redo = all_res_redo.fillna('NaN')
all_residues.update(all_res_redo)
order = ['Res '+str(x) for x in range(1, 307)]
all_residues = all_residues[order]
all_residues = all_residues.applymap(lambda x: x if not isinstance(x, str) else np.nan)

0.5415571046375395
0.6970969283522185
0.38330629549977147
0.35686351236041086
0.3951874654485591


#### Replicate 2

In [20]:
rep1_set, set_list_res = replicate(1, 'replicate_folder', '_gal_glu.csv')

all_residues1 = pd.concat(rep1_set, axis = 1)

all_res_redo = pd.concat(set_list_res, axis = 1)
all_res_redo = all_res_redo.fillna('NaN')
all_residues1.update(all_res_redo)
order = ['Res '+str(x) for x in range(1, 307)]
all_residues1 = all_residues1[order]
all_residues1 = all_residues1.applymap(lambda x: x if not isinstance(x, str) else np.nan)

0.7628694505817772
0.606201295831528
0.7956543179104758
0.3712752166338773
0.32681201937635457


#### Plotting the overall correlation

In [6]:
rep1 = [item for sublist in all_residues.values for item in sublist]
rep2 = [item for sublist in all_residues1.values for item in sublist]

fig  = go.Figure()
fig.add_trace(go.Scatter(x=rep1, y=rep2, marker=dict(
            color='#545555',
            size=8,
            opacity=0.5), mode = 'markers'))

corr = pd.Series(rep1).corr(pd.Series(rep2), method = 'pearson').round(2)
# fig.add_trace(go.Scatter(x=[-4, 6], y=[-4, 6], mode='lines'))
fig.update_xaxes(showline=True, linewidth=1, linecolor='black', mirror=True,
                showgrid=False)
fig.update_yaxes(showline=True, linewidth=1, linecolor='black', mirror=True,
                showgrid=False)
fig.add_annotation(
        x=-2.9,
        y=5.5,
        xref="x",
        yref="y",
        text="R="+str(corr),showarrow=False,
        font=dict(family="Arial",
                    size=16,
                    color="#545555"
                    ))
fig.update_layout(
    title="Mutation effects on protease activity",
    xaxis_title="Replicate 1",
    yaxis_title="Replicate 2",
    paper_bgcolor='rgba(255,255,255,100)',
    plot_bgcolor='rgba(255,255,255,100)',
    autosize=False,
    width=800,
    height=800,
    font=dict(family="Arial",
                    size=16,
                    color="#020202"
                    )
    )
fig.show()
# fig.write_image(fig_folder+"Fig1C_glu_gal.pdf")

In [19]:
replicates = pd.DataFrame({'rep1': rep1, 
                           'rep2':rep2} )
replicates = replicates.dropna()
stats.pearsonr(replicates['rep1'], replicates['rep2'])

(0.7171192981463025, 0.0)

### gc/gal condition

#### Replicate 1

In [20]:
rep1_set, set_list_res = replicate(0, 'replicate_folder_gc', '_gc.csv')
all_residues = pd.concat(rep1_set, axis = 1)

all_res_redo = pd.concat(set_list_res, axis = 1)
all_res_redo = all_res_redo.fillna('NaN')
all_residues.update(all_res_redo)
order = ['Res '+str(x) for x in range(1, 307)]
all_residues = all_residues[order]
all_residues = all_residues.applymap(lambda x: x if not isinstance(x, str) else np.nan)

#### Replicate 2

In [21]:
rep1_set, set_list_res = replicate(1, 'replicate_folder_gc', '_gc.csv')

all_residues1 = pd.concat(rep1_set, axis = 1)

all_res_redo = pd.concat(set_list_res, axis = 1)
all_res_redo = all_res_redo.fillna('NaN')
all_residues1.update(all_res_redo)
order = ['Res '+str(x) for x in range(1, 307)]
all_residues1 = all_residues1[order]
all_residues1 = all_residues1.applymap(lambda x: x if not isinstance(x, str) else np.nan)

#### Plotting correlation

In [22]:
rep1 = [item for sublist in all_residues.values for item in sublist]
rep2 = [item for sublist in all_residues1.values for item in sublist]

fig  = go.Figure()
fig.add_trace(go.Scatter(x=rep1, y=rep2, marker=dict(
            color='#545555',
            size=8,
            opacity=0.5), mode = 'markers'))

corr = pd.Series(rep1).corr(pd.Series(rep2), method = 'pearson').round(2)
# fig.add_trace(go.Scatter(x=[-4, 6], y=[-4, 6], mode='lines'))
fig.update_xaxes(showline=True, linewidth=1, linecolor='black', mirror=True,
                showgrid=False)
fig.update_yaxes(showline=True, linewidth=1, linecolor='black', mirror=True,
                showgrid=False)
fig.add_annotation(
        x=-6.9,
        y=5.5,
        xref="x",
        yref="y",
        text="R="+str(corr),showarrow=False,
        font=dict(family="Arial",
                    size=16,
                    color="#545555"
                    ))
fig.update_layout(
    title="Mutation effects on protease activity in presence of gc",
    xaxis_title="Replicate 1",
    yaxis_title="Replicate 2",
    paper_bgcolor='rgba(255,255,255,100)',
    plot_bgcolor='rgba(255,255,255,100)',
    autosize=False,
    width=800,
    height=800,
    font=dict(family="Arial",
                    size=16,
                    color="#020202"
                    )
    )
fig.show()
fig.write_image(fig_folder+"Fig1C_gc_gal.pdf")

In [23]:
replicates = pd.DataFrame({'rep1': rep1, 
                           'rep2':rep2} )
replicates = replicates.dropna()
stats.pearsonr(replicates['rep1'], replicates['rep2'])

(0.44242909193085217, 3.852433518016538e-300)

### gal/grl condition

#### replicate 1

In [24]:
rep1_set, set_list_res = replicate(0, 'replicate_folder_grl', '_grl.csv')
all_residues = pd.concat(rep1_set, axis = 1)

all_res_redo = pd.concat(set_list_res, axis = 1)
all_res_redo = all_res_redo.fillna('NaN')
all_residues.update(all_res_redo)
order = ['Res '+str(x) for x in range(1, 307)]
all_residues = all_residues[order]
all_residues = all_residues.applymap(lambda x: x if not isinstance(x, str) else np.nan)

#### replicate 2

In [25]:
rep1_set, set_list_res = replicate(1, 'replicate_folder_grl', '_grl.csv')

all_residues1 = pd.concat(rep1_set, axis = 1)

all_res_redo = pd.concat(set_list_res, axis = 1)
all_res_redo = all_res_redo.fillna('NaN')
all_residues1.update(all_res_redo)
order = ['Res '+str(x) for x in range(1, 307)]
all_residues1 = all_residues1[order]
all_residues1 = all_residues1.applymap(lambda x: x if not isinstance(x, str) else np.nan)

#### plotting correlation

In [26]:
rep1 = [item for sublist in all_residues.values for item in sublist]
rep2 = [item for sublist in all_residues1.values for item in sublist]

fig  = go.Figure()
fig.add_trace(go.Scatter(x=rep1, y=rep2, marker=dict(
            color='#545555',
            size=8,
            opacity=0.5), mode = 'markers'))

corr = pd.Series(rep1).corr(pd.Series(rep2), method = 'pearson').round(2)
# fig.add_trace(go.Scatter(x=[-4, 6], y=[-4, 6], mode='lines'))
fig.update_xaxes(showline=True, linewidth=1, linecolor='black', mirror=True,
                showgrid=False)
fig.update_yaxes(showline=True, linewidth=1, linecolor='black', mirror=True,
                showgrid=False)
fig.add_annotation(
        x=-6.9,
        y=5.5,
        xref="x",
        yref="y",
        text="R="+str(corr),showarrow=False,
        font=dict(family="Arial",
                    size=16,
                    color="#545555"
                    ))
fig.update_layout(
    title="Mutation effects on protease activity in presence of grl",
    xaxis_title="Replicate 1",
    yaxis_title="Replicate 2",
    paper_bgcolor='rgba(255,255,255,100)',
    plot_bgcolor='rgba(255,255,255,100)',
    autosize=False,
    width=800,
    height=800,
    font=dict(family="Arial",
                    size=16,
                    color="#020202"
                    )
    )
fig.show()
fig.write_image(fig_folder+"Fig1C_grl_gal.pdf")

In [27]:
replicates = pd.DataFrame({'rep1': rep1, 
                           'rep2':rep2} )
replicates = replicates.dropna()
stats.pearsonr(replicates['rep1'], replicates['rep2'])

(0.7907895279629658, 0.0)